## SDK code to create PRODUCT_Consistency_of_item_TotalCost_across_invoice_Weekdays_14d_vs_28d

Feature description:
>Consistency score of the product measured by the Cosine Similarity between the Distribution representing the cumulative TotalCost of item, categorized by their respective invoice's Weekday, for both the 14d and 28d periods.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['14d', '28d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

### Extract Date parts
 See [SDK reference for view columns](https://docs.featurebyte.com/latest/reference/core/view_column/)

 See [list of datetime transforms](https://docs.featurebyte.com/latest/about/glossary/#datetime-transforms)

In [ ]:
# Extract day_of_week date part from Timestamp column for INVOICEITEMS view.
invoiceitems_view["Weekday of invoice"] = invoiceitems_view["Timestamp"].dt.day_of_week

### Do window aggregation from INVOICEITEMS
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group INVOICEITEMS view by product entity (GroceryProductGuid) across different Weekday of
# invoices.
invoiceitems_view_by_product_across_weekday_of_invoice =\
invoiceitems_view.groupby(
    ['GroceryProductGuid'], category="Weekday of invoice"
)

In [ ]:
# Distribution representing the cumulative TotalCost of item, categorized by their respective
# invoice's Weekday, for the product over time.
feature_group =\
invoiceitems_view_by_product_across_weekday_of_invoice.aggregate_over(
    "TotalCost", method=fb.AggFunc.SUM,
    feature_names=[
        "PRODUCT_item_TotalCost_across_invoice_Weekdays"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get PRODUCT_item_TotalCost_across_invoice_Weekdays_14d object from feature group.
product_item_totalcost_across_invoice_weekdays_14d =\
feature_group["PRODUCT_item_TotalCost_across_invoice_Weekdays_14d"]
# Get PRODUCT_item_TotalCost_across_invoice_Weekdays_28d object from feature group.
product_item_totalcost_across_invoice_weekdays_28d =\
feature_group["PRODUCT_item_TotalCost_across_invoice_Weekdays_28d"]

In [ ]:
# Derive Consistency feature from cosine similarity between
# PRODUCT_item_TotalCost_across_invoice_Weekdays_14d
# and PRODUCT_item_TotalCost_across_invoice_Weekdays_28d
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d =\
product_item_totalcost_across_invoice_weekdays_14d.cd.cosine_similarity(
        product_item_totalcost_across_invoice_weekdays_28d
    )
# Give a name to new feature
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.name = \
"PRODUCT_Consistency_of_item_TotalCost_across_invoice_Weekdays_14d_vs_28d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 items'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 items"
).to_pandas()

In [ ]:
#Preview PRODUCT_Consistency_of_item_TotalCost_across_invoice_Weekdays_14d_vs_28d
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.update_description(
	"Consistency score of the product measured by the Cosine Similarity "
	"between the Distribution representing the cumulative TotalCost of "
	"item, categorized by their respective invoice's Weekday, for both the "
	"14d and 28d periods."
)
# See feature definition file
product_consistency_of_item_totalcost_across_invoice_weekdays_14d_vs_28d.definition